# Image API Web Scrapping

# IMDb Movies
![An image](https://static.amazon.jobs/teams/53/images/IMDb_Header_Page.jpg?1501027252)

**Este projeto consiste em treinar um sistema de recomendação de filmes utilizando as informações referentes aos filmes avaliados pelo público na plataforma IMDb.**
*   A extração dos dados será feita por técnicas de web scraping (crawler).

**Exemplo de aplicação prática: usuários receberão recomendações de filmes que estejam no mesmo cluster de sinopses de outros filmes que ele já tenha curtido.**

# Import das bibliotecas

In [6]:
import pandas as pd
import numpy as np
import requests
from pprint import pprint
from bs4 import BeautifulSoup
import re
import json
from urllib.request import Request, urlopen
# from lxml import html
import time
# import matplotlib.pyplot as plt
# import seaborn as sns
# import plotly.express as px
# from wordcloud import WordCloud
# from sklearn.feature_extraction.text import TfidfVectorizer
# from sklearn.cluster import KMeans
# from yellowbrick.cluster import KElbowVisualizer, SilhouetteVisualizer

# Web Scraping / Crawler

In [124]:
userAgents=[
    "Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) HeadlessChrome/74.0.3729.157 Safari/537.36",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_14_5) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.1 Safari/605.1.15"]

# url = 'https://www.imdb.com/chart/bottom/?ref_=chtmvm_ql_7'
# url = 'https://www.imdb.com/chart/moviemeter/?ref_=ft_cht_pop'
# url = 'https://www.imdb.com/chart/top-english-movies/?ref_=chtmvm_ql_4'
url = 'https://www.imdb.com/chart/top/?ref_=chtmvm_ql_3'

response = requests.get(url, headers={"User-agent": userAgents[1]})
response

<Response [200]>

In [125]:
html = response.text
html

'<!DOCTYPE html><html lang="en-US" xmlns:og="http://opengraphprotocol.org/schema/" xmlns:fb="http://www.facebook.com/2008/fbml"><head><meta charSet="utf-8"/><meta name="viewport" content="width=device-width"/><script>if(typeof uet === \'function\'){ uet(\'bb\', \'LoadTitle\', {wb: 1}); }</script><script>window.addEventListener(\'load\', (event) => {\n        if (typeof window.csa !== \'undefined\' && typeof window.csa === \'function\') {\n            var csaLatencyPlugin = window.csa(\'Content\', {\n                element: {\n                    slotId: \'LoadTitle\',\n                    type: \'service-call\'\n                }\n            });\n            csaLatencyPlugin(\'mark\', \'clickToBodyBegin\', 1694697164659);\n        }\n    })</script><title>IMDb Top 250 Movies</title><meta name="description" content="IMDb Top 250 as rated by regular IMDb voters" data-id="main"/><meta property="og:site_name" content="IMDb"/><meta property="og:title" content="IMDb Top 250 Movies"/><meta 

In [126]:
#BeautifulSoup
bs = BeautifulSoup(html)
pprint(bs)


<!DOCTYPE html>
<html lang="en-US" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraphprotocol.org/schema/"><head><meta charset="utf-8"/><meta content="width=device-width" name="viewport"/><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><script>window.addEventListener('load', (event) => {
        if (typeof window.csa !== 'undefined' && typeof window.csa === 'function') {
            var csaLatencyPlugin = window.csa('Content', {
                element: {
                    slotId: 'LoadTitle',
                    type: 'service-call'
                }
            });
            csaLatencyPlugin('mark', 'clickToBodyBegin', 1694697164659);
        }
    })</script><title>IMDb Top 250 Movies</title><meta content="IMDb Top 250 as rated by regular IMDb voters" data-id="main" name="description"/><meta content="IMDb" property="og:site_name"/><meta content="IMDb Top 250 Movies" property="og:title"/><meta content="IMDb Top 250 as rated b

## Title EN

In [127]:
titles = bs.find_all('h3', attrs={'class': 'ipc-title__text'})
titles

[<h3 class="ipc-title__text">IMDb Charts</h3>,
 <h3 class="ipc-title__text">1. Um Sonho de Liberdade</h3>,
 <h3 class="ipc-title__text">2. O Poderoso Chefão</h3>,
 <h3 class="ipc-title__text">3. Batman: O Cavaleiro das Trevas</h3>,
 <h3 class="ipc-title__text">4. O Poderoso Chefão II</h3>,
 <h3 class="ipc-title__text">5. 12 Homens e uma Sentença</h3>,
 <h3 class="ipc-title__text">6. A Lista de Schindler</h3>,
 <h3 class="ipc-title__text">7. O Senhor dos Anéis: O Retorno do Rei</h3>,
 <h3 class="ipc-title__text">8. Pulp Fiction - Tempo de Violência</h3>,
 <h3 class="ipc-title__text">9. O Senhor dos Anéis: A Sociedade do Anel</h3>,
 <h3 class="ipc-title__text">10. Três Homens em Conflito</h3>,
 <h3 class="ipc-title__text">11. Forrest Gump: O Contador de Histórias</h3>,
 <h3 class="ipc-title__text">12. Clube da Luta</h3>,
 <h3 class="ipc-title__text">13. O Senhor dos Anéis: As Duas Torres</h3>,
 <h3 class="ipc-title__text">14. A Origem</h3>,
 <h3 class="ipc-title__text">15. Star Wars: Epi

In [128]:
list_title_en = []
for x in titles[1:-12]:
  tit = (x.text).split(">")[0].strip()
  list_title_en.append(tit)

display(len(list_title_en))
list_title_en[:5]

250

['1. Um Sonho de Liberdade',
 '2. O Poderoso Chefão',
 '3. Batman: O Cavaleiro das Trevas',
 '4. O Poderoso Chefão II',
 '5. 12 Homens e uma Sentença']

## Year

In [129]:
list_years = []
years = bs.find_all('div', attrs={'class':'sc-b51a3d33-5 ibuRZu cli-title-metadata'})
for y in years:
  year = y.find('span', attrs={'class':'sc-b51a3d33-6 faLXbD cli-title-metadata-item'}).text
  list_years.append(year)
display(len(list_years))
list_years[:5]

250

['1994', '1972', '2008', '1974', '1957']

## Rating

In [130]:
ratings = bs.find_all('div', attrs={'class':'sc-e3e7b191-0 iKUUVe sc-b51a3d33-2 ccUQup cli-ratings-container'})
list_rating = []
for r in ratings:
  rating = r.find('span').text
  list_rating.append(rating[:3])

display(len(list_rating))
pprint(list_rating[:5])

250

['9.3', '9.2', '9.0', '9.0', '9.0']


## Genre, Title PT & Year

In [131]:
list_links = []
for a in bs.find_all('a', href=True):
  if '/title/' in a['href'] and 'https://www.imdb.com/'+ a['href'] not in list_links:
    list_links.append(('https://www.imdb.com/'+a['href'])[:-15])

#Remove duplicates
list_links = list(dict.fromkeys(list_links))
#Deleting first element
list_links = list_links[1:]

display(len(list_links))
list_links[:5]

250

['https://www.imdb.com//title/tt0111161/',
 'https://www.imdb.com//title/tt0068646/',
 'https://www.imdb.com//title/tt0468569/',
 'https://www.imdb.com//title/tt0071562/',
 'https://www.imdb.com//title/tt0050083/']

# Image

In [132]:
images = bs.find_all('img', class_='ipc-image')
    
image_urls = [img['src'] for img in images if 'src' in img.attrs]

display(len(image_urls))
image_urls[:5]

250

['https://m.media-amazon.com/images/M/MV5BNDE3ODcxYzMtY2YzZC00NmNlLWJiNDMtZDViZWM2MzIxZDYwXkEyXkFqcGdeQXVyNjAwNDUxODI@._V1_QL75_UX140_CR0,1,140,207_.jpg',
 'https://m.media-amazon.com/images/M/MV5BZjgwNzE5ODgtYzAyZC00YTZhLThhNDktMDVlOGNhYzk5NTVkXkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY207_CR3,0,140,207_.jpg',
 'https://m.media-amazon.com/images/M/MV5BM2E1ZjEyYWQtMjgyMy00ZTkwLThkM2QtN2YwM2NmYzAyYjE0XkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY207_CR8,0,140,207_.jpg',
 'https://m.media-amazon.com/images/M/MV5BOGM2M2Q0ZWQtZjc5NC00NDY4LWIxYTktMDE4ZjIyYTRlNTIyXkEyXkFqcGdeQXVyODc0OTEyNDU@._V1_QL75_UY207_CR4,0,140,207_.jpg',
 'https://m.media-amazon.com/images/M/MV5BODRmNWRiYmUtNGM2Yy00NTgwLTgxNzMtMGExYzI5NjllNjBhXkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY207_CR3,0,140,207_.jpg']

In [133]:
headers = {
          'authority': 'www.amazon.com.br',
          'accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7',
          'accept-language': 'pt-BR,pt;q=0.9,en-US;q=0.8,en;q=0.7',
          'cache-control': 'max-age=0',
          'device-memory': '8',
          'downlink': '10',
          'dpr': '1.875',
          'ect': '4g',
          'rtt': '50',
          'sec-ch-device-memory': '8',
          'sec-ch-dpr': '1.875',
          'sec-ch-ua': '"Chromium";v="110", "Not A(Brand";v="24", "Google Chrome";v="110"',
          'sec-ch-ua-mobile': '?0',
          'sec-ch-ua-platform': '"Windows"',
          'sec-ch-ua-platform-version': '"10.0.0"',
          'sec-ch-viewport-width': '455',
          'sec-fetch-dest': 'document',
          'sec-fetch-mode': 'navigate',
          'sec-fetch-site': 'none',
          'sec-fetch-user': '?1',
          'upgrade-insecure-requests': '1',
          'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/110.0.0.0 Safari/537.36',
          'viewport-width': '455',
          }

link = list_links[0]  # Apenas para teste
response = requests.get(link, headers=headers)
html = response.content
soup = BeautifulSoup(html, "html.parser")

image_tag = soup.find('img', class_='ipc-image')
if image_tag and 'srcset' in image_tag.attrs:
    image_tag = image_tag['srcset'].split(', ')
image_tag[-1][:-5]

'https://m.media-amazon.com/images/M/MV5BNDE3ODcxYzMtY2YzZC00NmNlLWJiNDMtZDViZWM2MzIxZDYwXkEyXkFqcGdeQXVyNjAwNDUxODI@._V1_QL75_UX380_CR0,4,380,562_.jpg'

In [134]:
headers = {
          'authority': 'www.amazon.com.br',
          'accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7',
          'accept-language': 'pt-BR,pt;q=0.9,en-US;q=0.8,en;q=0.7',
          'cache-control': 'max-age=0',
          'device-memory': '8',
          'downlink': '10',
          'dpr': '1.875',
          'ect': '4g',
          'rtt': '50',
          'sec-ch-device-memory': '8',
          'sec-ch-dpr': '1.875',
          'sec-ch-ua': '"Chromium";v="110", "Not A(Brand";v="24", "Google Chrome";v="110"',
          'sec-ch-ua-mobile': '?0',
          'sec-ch-ua-platform': '"Windows"',
          'sec-ch-ua-platform-version': '"10.0.0"',
          'sec-ch-viewport-width': '455',
          'sec-fetch-dest': 'document',
          'sec-fetch-mode': 'navigate',
          'sec-fetch-site': 'none',
          'sec-fetch-user': '?1',
          'upgrade-insecure-requests': '1',
          'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/110.0.0.0 Safari/537.36',
          'viewport-width': '455',
          }
############################################################
list_genre = []
list_title_pt = []
list_year = []
list_sinopse = []
list_images = []

for link in list_links:
  time.sleep(.5)
  response = requests.get(link, headers = headers)
  html = response.content
  soup = BeautifulSoup(html, "html.parser")

  #genre
  try:
    for genre in soup.find('span', {'class':'ipc-chip__text'}):
      genre = genre.text
      list_genre.append(genre)
  except:
      list_genre.append(np.nan)
      print('Nan')

  #title_PT and year
  try:
    for x in soup.find('title'):
      #title_pt
      title_pt = (x.text)[:-14].strip()
      list_title_pt.append(title_pt)
      #year
      year = (x.text)[-12:-8].strip()
      list_year.append(year)

  except:
    list_title_pt.append(np.nan)
    list_year.append(np.nan)

  #sinopse
  try:
    for sin in soup.find('span', {"data-testid":"plot-xl"}):
      sinopse = sin.text
      list_sinopse.append(sinopse)
  except:
    list_sinopse.append(np.nan)

  #image
  try:
    image_tag = soup.find('img', class_='ipc-image')
    if image_tag and 'srcset' in image_tag.attrs:
        list_images.append(image_tag['srcset'].split(', ')[-1][:-5])
    else:
        list_images.append(np.nan)
  except:
      list_images.append(np.nan)

  print(genre, title_pt, year, sinopse[:20], list_images[-1])

display(len(list_genre), len(list_title_pt), len(list_year), len(list_sinopse))
print(list_genre[:5])
print(list_title_pt[:5])
print(list_year[:5])
display(list_sinopse[:2])
print(list_images[:5])

Drama Um Sonho de Liberdade 1994 Dois homens presos s https://m.media-amazon.com/images/M/MV5BNDE3ODcxYzMtY2YzZC00NmNlLWJiNDMtZDViZWM2MzIxZDYwXkEyXkFqcGdeQXVyNjAwNDUxODI@._V1_QL75_UX380_CR0,4,380,562_.jpg
Policial O Poderoso Chefão 1972 O patriarca idoso de https://m.media-amazon.com/images/M/MV5BZjgwNzE5ODgtYzAyZC00YTZhLThhNDktMDVlOGNhYzk5NTVkXkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY562_CR7,0,380,562_.jpg
Ação Batman: O Cavaleiro das Trevas 2008 Quando a ameaça conh https://m.media-amazon.com/images/M/MV5BM2E1ZjEyYWQtMjgyMy00ZTkwLThkM2QtN2YwM2NmYzAyYjE0XkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY562_CR21,0,380,562_.jpg
Policial O Poderoso Chefão II 1974 Em 1950, Michael Cor https://m.media-amazon.com/images/M/MV5BOGM2M2Q0ZWQtZjc5NC00NDY4LWIxYTktMDE4ZjIyYTRlNTIyXkEyXkFqcGdeQXVyODc0OTEyNDU@._V1_QL75_UY562_CR11,0,380,562_.jpg
Policial 12 Homens e uma Sentença 1957 O julgamento de um a https://m.media-amazon.com/images/M/MV5BODRmNWRiYmUtNGM2Yy00NTgwLTgxNzMtMGExYzI5NjllNjBhXkEyXkFqcGdeQXVyMTAzM

250

250

250

250

['Drama', 'Policial', 'Ação', 'Policial', 'Policial']
['Um Sonho de Liberdade', 'O Poderoso Chefão', 'Batman: O Cavaleiro das Trevas', 'O Poderoso Chefão II', '12 Homens e uma Sentença']
['1994', '1972', '2008', '1974', '1957']


['Dois homens presos se reúnem ao longo de vários anos, encontrando consolo e eventual redenção através de atos de decência comum.',
 'O patriarca idoso de uma dinastia do crime organizado transfere o controle de seu império clandestino para seu filho relutante.']

['https://m.media-amazon.com/images/M/MV5BNDE3ODcxYzMtY2YzZC00NmNlLWJiNDMtZDViZWM2MzIxZDYwXkEyXkFqcGdeQXVyNjAwNDUxODI@._V1_QL75_UX380_CR0,4,380,562_.jpg', 'https://m.media-amazon.com/images/M/MV5BZjgwNzE5ODgtYzAyZC00YTZhLThhNDktMDVlOGNhYzk5NTVkXkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY562_CR7,0,380,562_.jpg', 'https://m.media-amazon.com/images/M/MV5BM2E1ZjEyYWQtMjgyMy00ZTkwLThkM2QtN2YwM2NmYzAyYjE0XkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY562_CR21,0,380,562_.jpg', 'https://m.media-amazon.com/images/M/MV5BOGM2M2Q0ZWQtZjc5NC00NDY4LWIxYTktMDE4ZjIyYTRlNTIyXkEyXkFqcGdeQXVyODc0OTEyNDU@._V1_QL75_UY562_CR11,0,380,562_.jpg', 'https://m.media-amazon.com/images/M/MV5BODRmNWRiYmUtNGM2Yy00NTgwLTgxNzMtMGExYzI5NjllNjBhXkEyXkFqcGdeQXVyMTAzMDM4MjM0._V1_QL75_UY562_CR7,0,380,562_.jpg']


## DataFrame

In [117]:
list_sinopse

['Dois homens presos se reúnem ao longo de vários anos, encontrando consolo e eventual redenção através de atos de decência comum.',
 'O patriarca idoso de uma dinastia do crime organizado transfere o controle de seu império clandestino para seu filho relutante.',
 'Quando a ameaça conhecida como O Coringa surge de seu passado, causa estragos e caos nas pessoas de Gotham. O Cavaleiro das Trevas deve aceitar um dos maiores testes para combater a injustiça.',
 'Em 1950, Michael Corleone, agora à frente da família, tenta expandir o negócio do crime a Las Vegas, Los Angeles e Cuba. Paralelamente, é revelada a história de Vito Corleone, e de como saiu da Sicília e chegou a Nova Iorque.',
 'O julgamento de um assassinato em Nova Iorque é frustrado por um único membro, cujo ceticismo força o júri a considerar cuidadosamente as evidências antes de dar o veredito.',
 'Na Polônia ocupada pelos alemães durante a Segunda Guerra Mundial, o industrial Oskar Schindler começa a ser preocupar com seus 

In [118]:
list_sinopse = [sinopse for sinopse in list_sinopse if sinopse != '']
len(list_sinopse)

250

In [135]:
df = pd.DataFrame({'title_pt':list_title_pt,
                   'title_en':list_title_en,
                   'year':list_year,
                   'rating':list_rating,
                   'genre':list_genre,
                   'sinopse':list_sinopse,
                   'image':image_urls})
display(df.head())

title_pt                           title_en  year  \
0           Um Sonho de Liberdade           1. Um Sonho de Liberdade  1994   
1               O Poderoso Chefão               2. O Poderoso Chefão  1972   
2  Batman: O Cavaleiro das Trevas  3. Batman: O Cavaleiro das Trevas  2008   
3            O Poderoso Chefão II            4. O Poderoso Chefão II  1974   
4        12 Homens e uma Sentença        5. 12 Homens e uma Sentença  1957   

  rating     genre                                            sinopse  \
0    9.3     Drama  Dois homens presos se reúnem ao longo de vário...   
1    9.2  Policial  O patriarca idoso de uma dinastia do crime org...   
2    9.0      Ação  Quando a ameaça conhecida como O Coringa surge...   
3    9.0  Policial  Em 1950, Michael Corleone, agora à frente da f...   
4    9.0  Policial  O julgamento de um assassinato em Nova Iorque ...   

                                               image  
0  https://m.media-amazon.com/images/M/MV5BNDE3OD...  
1  https://m.media-amazon.com/images/M/MV5BZjgwNz...  
2  https://m.media-amazon.com/images/M/MV5BM2E1Zj...  
3  https://m.media-amazon.com/images/M/MV5BOGM2M2...  
4  https://m.media-amazon.com/images/M/MV5BODRmNW...

# Export df to csv

In [136]:
from datetime import datetime
today = datetime.today().strftime('%Y%m%d')
today

'20230914'

In [137]:
path_to_export = './api/app/database'
df.to_csv(f'{path_to_export}/4_{today}.csv', sep = ';',index = False)

# Merge with historical data

In [138]:
#Merge with historical data
from glob import glob

#loading MES
list_files = []
for file in glob(path_to_export + '/*.csv'):
    list_files.append(file)

#appending each tag file in a list
list_df = []
c = 0
for file in list_files:
    print(f'{c+1} of {len(list_files)} | {file}')
    df_temp = pd.read_csv(  file, sep = ';')
    list_df.append(df_temp)
    c += 1

#mergin all files
df_historical = pd.concat(list_df, axis = 0, copy = False)
df_historical = df_historical.drop_duplicates(subset=['title_pt'], keep = 'last')
df_historical = df_historical.reset_index(drop = True)
display(df_historical.shape)
display(df_historical)

1 of 5 | ./api/app/database\1_20230914.csv
2 of 5 | ./api/app/database\2_20230914.csv
3 of 5 | ./api/app/database\3_20230914.csv
4 of 5 | ./api/app/database\4_20230914.csv
5 of 5 | ./api/app/database\all_movies.csv


(496, 7)

title_pt                 title_en  year  rating      genre  \
0         Os Sete Samurais     22. Os Sete Samurais  1954     8.6       Ação   
1           Cidade de Deus       26. Cidade de Deus  2002     8.6   Policial   
2            A Vida é Bela        27. A Vida é Bela  1997     8.6    Comédia   
3      A Viagem de Chihiro  32. A Viagem de Chihiro  2001     8.6   Animação   
4                 Parasita             35. Parasita  2019     8.5      Drama   
..                     ...                      ...   ...     ...        ...   
491                  Tenet                    Tenet  2020     7.3       Ação   
492                Maestro                  Maestro  2023     6.7  Biografia   
493      Top Gun: Maverick        Top Gun: Maverick  2022     8.3       Ação   
494  Os Pequenos Vestígios    Os Pequenos Vestígios  2021     6.3   Policial   
495            Minha Culpa              Minha Culpa  2023     6.2      Drama   

                                               sinopse  \
0    Uma aldeia pobre sob a ameaça de bandidos recr...   
1    Os caminhos de duas crianças divergem nas fave...   
2    Quando um bibliotecário judeu e seu filho se t...   
3    Durante a mudança de casa, uma menina de dez a...   
4    Desempregados, a família de Ki-taek (Song Kang...   
..                                                 ...   
491  O projeto é descrito como um épico de ação que...   
492  O amor complexo de Leonard Bernstein e Felicia...   
493  Após mais de trinta anos de serviço como um do...   
494     Dois polícias localizam um assassino em série.   
495  Uma jovem tem que deixar sua cidade, namorado ...   

                                                 image  
0    https://m.media-amazon.com/images/M/MV5BN2RhYz...  
1    https://m.media-amazon.com/images/M/MV5BOTMwYj...  
2    https://m.media-amazon.com/images/M/MV5BYTY3M2...  
3    https://m.media-amazon.com/images/M/MV5BMjlmZm...  
4    https://m.media-amazon.com/images/M/MV5BYWZjMj...  
..                                                 ...  
491  https://m.media-amazon.com/images/M/MV5BMTkwZD...  
492  https://m.media-amazon.com/images/M/MV5BZDczMm...  
493  https://m.media-amazon.com/images/M/MV5BMGU1MW...  
494  https://m.media-amazon.com/images/M/MV5BOGFlNT...  
495  https://m.media-amazon.com/images/M/MV5BNWM0ZD...  

[496 rows x 7 columns]

# Export historical data

In [123]:
df_historical.to_csv(f'{path_to_export}/all_movies.csv', sep = ';',index = False)